# Preparation

In [1]:
import torch
import torchvision
import torch.nn as nn
import torch.nn.functional as F
import torchvision.transforms as T
from torchvision import models
from torch.utils.data import DataLoader
import torch.optim as optim
from torchvision import datasets
from torch.utils.data.dataset import Subset
import matplotlib.pyplot as plt
import random
import os
import enum
import numpy as np
import pandas as pd
import collections

C:\Users\karub\Anaconda3\envs\pytorch\lib\site-packages\numpy\_distributor_init.py:30: UserWarning: loaded more than 1 DLL from .libs:
C:\Users\karub\Anaconda3\envs\pytorch\lib\site-packages\numpy\.libs\libopenblas.GK7GX5KEQ4F6UYO3P26ULGBQYHGQO7J4.gfortran-win_amd64.dll
C:\Users\karub\Anaconda3\envs\pytorch\lib\site-packages\numpy\.libs\libopenblas.NOIJJG62EMASZI6NYURL6JBKM4EVBGM7.gfortran-win_amd64.dll
  warnings.warn("loaded more than 1 DLL from .libs:"


# Create dataset

In [2]:
class QuestionType(enum.Enum):
    WHICH_ONE = 'which_one'
    IS_IN = 'is_in'
    COMP = 'comp'
class DataSet(enum.Enum):
    MNIST = 'mnist'
    FASHION = 'fashion'
    KMNIST = 'kmnist'
    CIFAR10 = 'cifar-10'

get_question_type = {QuestionType.WHICH_ONE: 'which_one',
                     QuestionType.IS_IN: 'is_in',
                     QuestionType.COMP: 'comp'}
get_dataset_name = {DataSet.MNIST: 'mnist',
                    DataSet.FASHION: 'fashion', 
                    DataSet.KMNIST: 'kmnist',
                    DataSet.CIFAR10: 'cifar-10'}

In [3]:
def prepare_mnist_data(batch_size):
    ordinary_train_dataset = datasets.MNIST(root='./data/mnist', train=True, transform=T.ToTensor(), download=True)
    test_dataset = datasets.MNIST(root='./data/mnist', train=False, transform=T.ToTensor())
    train_loader = torch.utils.data.DataLoader(dataset=ordinary_train_dataset, batch_size=batch_size, shuffle=False, num_workers=0)
    test_loader = torch.utils.data.DataLoader(dataset=test_dataset, batch_size=batch_size, shuffle=False, num_workers=0)
    full_train_loader = torch.utils.data.DataLoader(dataset=ordinary_train_dataset, batch_size=len(ordinary_train_dataset.data), shuffle=False, num_workers=0)
    num_classes = len(ordinary_train_dataset.classes)
    return full_train_loader, train_loader, test_loader

def prepare_kmnist_data(batch_size):
    ordinary_train_dataset = datasets.KMNIST(root='./data/KMNIST', train=True, transform=T.ToTensor(), download=True)
    test_dataset = datasets.KMNIST(root='./data/KMNIST', train=False, transform=T.ToTensor())
    train_loader = torch.utils.data.DataLoader(dataset=ordinary_train_dataset, batch_size=batch_size, shuffle=False, num_workers=0)
    test_loader = torch.utils.data.DataLoader(dataset=test_dataset, batch_size=batch_size, shuffle=False, num_workers=0)
    full_train_loader = torch.utils.data.DataLoader(dataset=ordinary_train_dataset, batch_size=len(ordinary_train_dataset.data), shuffle=False, num_workers=0)
    num_classes = len(ordinary_train_dataset.classes)
    return full_train_loader, train_loader, test_loader

def prepare_fashion_data(batch_size):
    ordinary_train_dataset = datasets.FashionMNIST(root='./data/FashionMnist', train=True, transform=T.ToTensor(), download=True)
    test_dataset = datasets.FashionMNIST(root='./data/FashionMnist', train=False, transform=T.ToTensor())
    train_loader = torch.utils.data.DataLoader(dataset=ordinary_train_dataset, batch_size=batch_size, shuffle=False, num_workers=0)
    test_loader = torch.utils.data.DataLoader(dataset=test_dataset, batch_size=batch_size, shuffle=False, num_workers=0)
    full_train_loader = torch.utils.data.DataLoader(dataset=ordinary_train_dataset, batch_size=len(ordinary_train_dataset.data), shuffle=False, num_workers=0)
    num_classes = len(ordinary_train_dataset.classes)
    return full_train_loader, train_loader, test_loader

#torchvision.datasets.CIFAR10.url="http://www.cs.toronto.edu/~kriz/cifar-10-python.tar.gz"
def prepare_cifar10_data(batch_size: int) -> [DataLoader, DataLoader, DataLoader, DataLoader]:
    train_transform = T.Compose(
        [T.ToTensor(), # transforms.RandomHorizontalFlip(), transforms.RandomCrop(32,4),
         T.Normalize((0.4914, 0.4822, 0.4465), (0.247, 0.243, 0.261))])
    test_transform = T.Compose(
        [T.ToTensor(),
         T.Normalize((0.4914, 0.4822, 0.4465), (0.247, 0.243, 0.261))])
    train_dataset = datasets.CIFAR10(root='./data', train=True, transform=train_transform, download=True)
    test_dataset = datasets.CIFAR10(root='./data', train=False, transform=test_transform)
    train_loader = torch.utils.data.DataLoader(dataset=train_dataset, batch_size=batch_size, shuffle=False, num_workers=0)
    test_loader = torch.utils.data.DataLoader(dataset=test_dataset, batch_size=batch_size, shuffle=False, num_workers=0)
    full_train_loader = torch.utils.data.DataLoader(dataset=train_dataset, batch_size=len(train_dataset.data), shuffle=False, num_workers=0)
    return full_train_loader, train_loader, test_loader

full_train_loader_fashion, train_loader_fashion, test_loader_fashion = prepare_fashion_data(256)
datas_fashion, labels_fashion = next(iter(full_train_loader_fashion))
full_train_loader_kmnist, train_loader_kmnist, test_loader_kmnist = prepare_kmnist_data(256)
datas_kmnist, labels_kmnist = next(iter(full_train_loader_kmnist))
full_train_loader_mnist, train_loader_mnist, test_loader_mnist = prepare_mnist_data(256)
datas_mnist, labels_mnist = next(iter(full_train_loader_mnist))
full_train_loader_cifar, train_loader_cifar, test_loader_cifar = prepare_cifar10_data(256)
datas_cifar, labels_cifar = next(iter(full_train_loader_cifar))

Files already downloaded and verified


In [6]:
def get_random_dataloader(full_train_loader: DataLoader, batch_size: int) -> [DataLoader, DataLoader]:
    datas, labels = next(iter(full_train_loader))
    count_list, count_index_list, delete_index_list = [0 for i in range(10)], [], []
    index_list = list(range(len(datas)))
    #random.shuffle(index_list)
    for index in index_list:
        target = labels[index].tolist()
        if count_list[target] >= 1000:
            delete_index_list.append(index)
        else:
            count_list[target] += 1
            count_index_list.append(index)
            
    datas_normal = np.delete(datas, delete_index_list, 0)
    labels_normal = np.delete(labels, delete_index_list, 0)
    
    datas_comp_pretrained = np.delete(datas, count_index_list, 0)
    labels_comp_pretrained = np.delete(labels, count_index_list, 0)
    
    random_train_matrix_dataset = torch.utils.data.TensorDataset(datas_normal, labels_normal.float())
    full_random_train_loader = torch.utils.data.DataLoader(dataset=random_train_matrix_dataset, batch_size=labels_normal.shape[0], shuffle=False, num_workers=0)
    random_train_loader = torch.utils.data.DataLoader(dataset=random_train_matrix_dataset, batch_size=batch_size, shuffle=False, num_workers=0)
    
    random_train_matrix_dataset_comp_pretrained = torch.utils.data.TensorDataset(datas_comp_pretrained, labels_comp_pretrained.float())
    full_random_train_loader_comp_pretrained = torch.utils.data.DataLoader(dataset=random_train_matrix_dataset_comp_pretrained, batch_size=labels_comp_pretrained.shape[0], shuffle=False, num_workers=0)
    random_train_loader_comp_pretrained = torch.utils.data.DataLoader(dataset=random_train_matrix_dataset_comp_pretrained, batch_size=batch_size, shuffle=False, num_workers=0)
    
    return full_random_train_loader, random_train_loader, full_random_train_loader_comp_pretrained, random_train_loader_comp_pretrained
full_random_train_loader_fashion, random_train_loader_fashion, full_random_train_loader_comp_pretrained_fashion, random_train_loader_comp_pretrained_fashion = get_random_dataloader(full_train_loader_fashion, 64)

In [40]:
def generate_comp_label(single_class_assigned: int,
                         all_class_size: int) -> list:
    
    all_class_set = [i for i in range(all_class_size)]
    all_class_set.remove(single_class_assigned)
    
    comp_class = random.choice(all_class_set)
    temporary_label_list = [1 for i in range(all_class_size)]
    
    temporary_label_list[comp_class] = 0
    
    return temporary_label_list

#def generate_comp_label(single_class_assigned: int,
#                         all_class_size: int) -> list:
#        
#    temporary_label_list = [1 for i in range(all_class_size)]
#    if single_class_assigned == 0:
#        temporary_label_list[1] = 0
#    elif single_class_assigned == 1:
#        temporary_label_list[0] = 0
#    else:
#        comp_class = random.choice([0, 1])
#        temporary_label_list[comp_class] = 0
#        
#    return temporary_label_list

temporary_label_list = generate_comp_label(single_class_assigned=3, 
                                            all_class_size=10)

temporary_label_list

[1, 1, 1, 1, 1, 1, 0, 1, 1, 1]

In [13]:
def generate_dataloader_with_comp_label(full_random_train_loader: DataLoader,
                                       batch_size: int) ->[DataLoader, int, int]:
    
    for i, (datas, labels) in enumerate(full_random_train_loader):
        all_class_size = torch.max(labels) + 1 # K is number of classes, full_train_loader is full batch
        all_class_size = int(all_class_size.tolist())
        
    comp_labels_tensor = generate_comp_labels(labels, all_class_size)
    comp_labels_matrix_dataset = torch.utils.data.TensorDataset(datas, comp_labels_tensor.float())
    
    comp_labels_matrix_train_loader = torch.utils.data.DataLoader(dataset=comp_labels_matrix_dataset, batch_size=batch_size, shuffle=False, num_workers=0)
    full_comp_labels_matrix_train_loader = torch.utils.data.DataLoader(dataset=comp_labels_matrix_dataset, batch_size=datas.shape[0], shuffle=False, num_workers=0)
    dimension = int(datas.reshape(-1).shape[0]/datas.shape[0])
    return full_comp_labels_matrix_train_loader, comp_labels_matrix_train_loader, dimension, all_class_size

In [14]:
from traitlets.traitlets import Integer
# Unclear!!!
DataSet_2_DataLoader_generator = {
    DataSet.MNIST: prepare_mnist_data,
    DataSet.FASHION: prepare_fashion_data,
    DataSet.KMNIST: prepare_kmnist_data,
    DataSet.CIFAR10: prepare_cifar10_data
}

def preparence(dataset: DataSet, batch_size: int):
    dataloader_generator = DataSet_2_DataLoader_generator[dataset]
    full_train_loader, train_loader, test_loader = dataloader_generator(batch_size)
    full_random_train_loader, random_train_loader = get_random_dataloader(full_train_loader, batch_size)
    
    return full_random_train_loader, random_train_loader, test_loader

full_random_train_loader, random_train_loader, test_loader = preparence(DataSet.FASHION, 256)

ValueError: too many values to unpack (expected 2)

In [ ]:
def transform_scalar_to_array(labels: torch.tensor, all_class_size: int) -> torch.Tensor:
    outputs = []
    for label in labels:
        label = int(label.tolist())
        label_full_size = [0] * all_class_size
        label_full_size[label] = 1
        outputs.append(label_full_size)
    
    outputs = torch.tensor(outputs)
    
    return outputs

# Model excution

In [15]:
import torch.nn as nn
import torch
import math
import torch.nn.functional as F

def mae_loss(outputs, labels):
    sm_outputs = F.softmax(outputs, dim=1)
    loss_fn = nn.L1Loss(reduction='none')
    loss_matrix = loss_fn(sm_outputs, labels.float())
    sample_loss = loss_matrix.sum(dim=-1)
    return sample_loss
    
def mse_loss(outputs, labels):
    sm_outputs = F.softmax(outputs, dim=1)
    loss_fn = nn.MSELoss(reduction='none')
    loss_matrix = loss_fn(sm_outputs, labels.float())
    sample_loss = loss_matrix.sum(dim=-1)
    return sample_loss

def gce_loss(outputs, labels):
    q = 0.7
    sm_outputs = F.softmax(outputs, dim=1)
    pow_outputs = torch.pow(sm_outputs, q)
    sample_loss = (1-(pow_outputs*labels).sum(dim=1))/q # n
    return sample_loss

def phuber_ce_loss(outputs, labels):
    trunc_point = 0.1
    n = labels.shape[0]
    soft_max = nn.Softmax(dim=1)
    sm_outputs = soft_max(outputs)
    final_outputs = sm_outputs * labels
    final_confidence = final_outputs.sum(dim=1)
    ce_index = (final_confidence > trunc_point)
    sample_loss = torch.zeros(n).to(device)

    if ce_index.sum() > 0:
        ce_outputs = outputs[ce_index,:]
        logsm = nn.LogSoftmax(dim=-1)
        logsm_outputs = logsm(ce_outputs)
        final_ce_outputs = logsm_outputs * labels[ce_index,:]
        sample_loss[ce_index] = - final_ce_outputs.sum(dim=-1)

    linear_index = (final_confidence <= trunc_point)

    if linear_index.sum() > 0:
        sample_loss[linear_index] = -math.log(trunc_point) + (-1/trunc_point)*final_confidence[linear_index] + 1

    return sample_loss

def ce_loss(outputs, labels):
    logsm = nn.LogSoftmax(dim=1)
    logsm_outputs = logsm(outputs)
    final_outputs = logsm_outputs * labels
    sample_loss = - final_outputs.sum(dim=1)
    return sample_loss

def W_O_loss(loss_fn_, outputs, labels, device, question_class_size, all_class_size):
    n, k = labels.shape[0], labels.shape[1]
    temp_loss = torch.zeros(n, k).to(device)
    for i in range(k):
        tempY = torch.zeros(n, k).to(device)
        tempY[:, i] = 1.0
        temp_loss[:, i] = loss_fn_(outputs, tempY)
        
    candidate_loss = (temp_loss * labels).sum(dim=1)
    noncandidate_loss = (temp_loss * (1-labels)).sum(dim=1)
    total_loss = candidate_loss - ((all_class_size - question_class_size) * (all_class_size - question_class_size - 1))/(question_class_size * (2*all_class_size - question_class_size - 1.0)) * noncandidate_loss
    average_loss = total_loss.mean()
    return average_loss

def I_I_loss(loss_fn_, outputs, labels, device, question_class_size, all_class_size):
    n, k = labels.shape[0], labels.shape[1]
    temp_loss = torch.zeros(n, k).to(device)
    for i in range(k):
        tempY = torch.zeros(n, k).to(device)
        tempY[:, i] = 1.0
        temp_loss[:, i] = loss_fn_(outputs, tempY)
        
    candidate_loss = (temp_loss * labels).sum(dim=1)
    noncandidate_loss = (temp_loss * (1-labels)).sum(dim=1)
    total_loss = candidate_loss - (2*question_class_size**2 + all_class_size**2 - all_class_size*(2*question_class_size + 1))/(2*question_class_size * (all_class_size - question_class_size)) * noncandidate_loss
    average_loss = total_loss.mean()
    return average_loss

def comp_loss(loss_fn_, outputs, labels, device, all_class_size):
    n, k = labels.shape[0], labels.shape[1]
    temp_loss = torch.zeros(n, k).to(device)
    for i in range(k):
        tempY = torch.zeros(n, k).to(device)
        tempY[:, i] = 1.0
        temp_loss[:, i] = loss_fn_(outputs, tempY)
        
    candidate_loss = (temp_loss * labels).sum(dim=1)
    noncandidate_loss = (temp_loss * (1-labels)).sum(dim=1)
    total_loss = candidate_loss - (all_class_size - 2) * noncandidate_loss
    average_loss = total_loss.mean()
    return average_loss


In [16]:
class mlp_model(nn.Module):
    def __init__(self, input_dim, hidden_dim, output_dim):
        super(mlp_model, self).__init__()
        self.fc1 = nn.Linear(input_dim, hidden_dim)
        self.relu1 = nn.ReLU()
        self.fc2 = nn.Linear(hidden_dim, output_dim)

    def forward(self, x):
        out = x.view(-1, self.num_flat_features(x))
        out = self.fc1(out)
        out = self.relu1(out)
        out = self.fc2(out)
        return out

    def num_flat_features(self, x):
        size = x.size()[1:]
        num_features = 1
        for s in size:
            num_features *= s
        return num_features

In [17]:
# ResNet-18 を作成する。
resnet = models.resnet18(pretrained=True)

# 出力層の出力数を ImageNet の 1000 からこのデータセットのクラス数である 2 に置き換える。
resnet.fc = nn.Linear(resnet.fc.in_features, 10)


In [18]:
def accuracy_check(loader, model, device):
    with torch.no_grad():
        total, num_samples = 0, 0
        for images, labels in loader:
            labels, images = labels.to(device), images.to(device)
            outputs = model(images)
            _, predicted = torch.max(outputs.data, 1)
            total += (predicted == labels).sum().item()
            num_samples += labels.size(0) 
    return total / num_samples

In [19]:
def loss_check(loader, model, criterion, device, all_class_size):
    with torch.no_grad():
        total, num_samples = 0, 0
        for images, labels in loader:
            labels, images = labels.to(device), images.to(device)
            outputs = model(images)
            labels = transform_scalar_to_array(labels, all_class_size)
            labels = labels.to(device)
            loss = criterion(outputs,labels)
            total += loss.sum().item()
            num_samples += labels.size(0) 
    return total / num_samples

In [20]:
def show_loss(epoch,max_epoch, loss):
    print('TRAIN EPOCH[{:03}/{:03}] LOSS:{:03f}%'.format(epoch, max_epoch, loss))    
def show_eval_loss(epoch,max_epoch, loss, is_val):
    if is_val:
        print('EVAL TEST EPOCH[{:03}/{:03}] LOSS:{:03f}%'.format(epoch, max_epoch, loss))
    else:
        print('EVAL TRAIN EPOCH[{:03}/{:03}] LOSS:{:03f}%'.format(epoch, max_epoch, loss))
def show_acc(epoch,max_epoch, acc, is_val):
    if is_val:
        print('TEST EPOCH[{:03}/{:03}] ACC:{:03f}%'.format(epoch, max_epoch, acc*100))
    else:
        print('TRAIN EPOCH[{:03}/{:03}] ACC:{:03f}%'.format(epoch, max_epoch, acc*100))

In [21]:
DEVICE = torch.device('cuda:0') if torch.cuda.is_available() else torch.device('cpu')
DEVICE

device(type='cuda', index=0)

In [52]:
def Train(model, 
          question_type, 
          question_class_size, 
          all_class_size, 
          criterion, 
          optimizer, 
          data_loader, 
          device, 
          epoch, 
          max_epoch):
        
    total_loss_train = 0.0
    model.train()

    for n, (data, label) in enumerate(data_loader):
        optimizer.zero_grad()
        data = data.to(device)
        label = label.to(device)
        output = model(data)
        if question_type == QuestionType.WHICH_ONE:
            loss = W_O_loss(criterion, output, label.float(), device, question_class_size, all_class_size)
        elif question_type == QuestionType.IS_IN:
            loss = I_I_loss(criterion, output, label.float(), device, question_class_size, all_class_size)
        elif question_type == QuestionType.COMP:
            loss = comp_loss(criterion, output, label.float(), device, all_class_size)
        else:
            loss = criterion(output,label)

        loss.backward()
        optimizer.step()
        total_loss_train += loss.item()

    show_loss(epoch+1, max_epoch, total_loss_train/(n+1))
    print()

    return total_loss_train/(n+1), model

In [53]:
def Eval(index,
        model, 
        evaluation_data_loader_train, 
        evaluation_data_loader_test,
        all_class_size,
        criterion,
        device, 
        epoch, 
        max_epoch):
    
    model.eval()
    if index == 'acc':
        total_acc_train = accuracy_check(evaluation_data_loader_train, model, device)
        total_acc_test = accuracy_check(evaluation_data_loader_test, model, device)

        show_acc(epoch+1, max_epoch, total_acc_train, is_val=False)
        print()
        show_acc(epoch+1, max_epoch, total_acc_test, is_val=True)
        print()

        return total_acc_train , total_acc_test, model
    elif index == 'loss':
        total_loss_train = loss_check(evaluation_data_loader_train, model, criterion, device, all_class_size)
        total_loss_test = loss_check(evaluation_data_loader_test, model, criterion, device, all_class_size)
        show_eval_loss(epoch+1, max_epoch, total_loss_train, is_val=False)
        print()
        show_eval_loss(epoch+1, max_epoch, total_loss_test, is_val=True)
        print()

        return total_loss_train , total_loss_test, model
        

In [54]:
get_loss_function = {ce_loss: 'CE_LOSS', 
                     mae_loss: 'MAE_LOSS'}

In [55]:
from tqdm.notebook import tqdm
import collections

In [56]:
def Train_Eval(index,
              dataset, 
              question_type, 
              question_class_size, 
              model_name, 
              batch_size, 
              loss_fn, 
              EPOCHS):
    print(f'START: {question_type}, {question_class_size}')
    
    if question_type == QuestionType.COMP:
        full_labels_matrix_train_loader, labels_matrix_train_loader, dimension, all_class_size = generate_dataloader_with_comp_label(full_random_train_loader,
                                                                                                                                              batch_size)
                                                                             
    else:
        full_labels_matrix_train_loader, labels_matrix_train_loader, dimension, all_class_size = generate_dataloader_with_Q_A_label(full_random_train_loader,
                                                                                                                                           question_type,
                                                                                                                                           question_class_size,
                                                                                                                                           batch_size)
    full_datas, full_labels = next(iter(full_labels_matrix_train_loader))
    counter = collections.Counter(torch.sum(full_labels, 1).int().tolist())
    print(counter)
    
    
    DEVICE = torch.device('cuda:0') if torch.cuda.is_available() else torch.device('cpu')
    #DEVICE = torch.device('mps')
    index=index
    
    if model_name == 'MLP':
        model = mlp_model(input_dim=dimension, hidden_dim=500, output_dim=all_class_size).to(DEVICE)
    elif model_name == 'ResNet':
        model = models.resnet18(pretrained=True)
        model.fc = nn.Linear(model.fc.in_features, 10)
        
    model.to(DEVICE)
    optimizer = optim.Adam(model.parameters(), lr=0.001, weight_decay=0.0001)

    train_index_list = []
    eval_train_index_list = []
    eval_test_index_list = []
    #results_df = pd.DataFrame(columns=["index", "dataset", "epoch", "question_type", "question_class_size", "model", "loss_function", "train_index", "train_index", "test_index"])
    results_df = []
    for epoch in tqdm(range(EPOCHS)):
        train_index, model = Train(model=model, 
                                  question_type=question_type,
                                  question_class_size=question_class_size,
                                  all_class_size=all_class_size,
                                  criterion=loss_fn,
                                  optimizer=optimizer, 
                                  data_loader=labels_matrix_train_loader,
                                  device=DEVICE, 
                                  epoch=epoch, 
                                  max_epoch=EPOCHS)
        
        eval_train_index, eval_test_index, model = Eval(index=index,
                                                        model=model, 
                                                        evaluation_data_loader_train=random_train_loader, 
                                                        evaluation_data_loader_test=test_loader,
                                                        all_class_size=all_class_size,
                                                        criterion=loss_fn,
                                                        device=DEVICE, 
                                                        epoch=epoch, 
                                                        max_epoch=EPOCHS)

        train_index_list.append(train_index)
        eval_train_index_list.append(eval_train_index)
        eval_test_index_list.append(eval_test_index)

        result_df = pd.DataFrame({'index': [index],
                                  'dataset': [get_dataset_name[dataset]],
                                  'epoch': [epoch+1],
                                  'question_type': [get_question_type[question_type]], 
                                  'question_class_size': [question_class_size], 
                                  'model': [model_name],
                                  'loss_function': [get_loss_function[loss_fn]],
                                  'train_index': [train_index],
                                  'eval_train_index': [eval_train_index],
                                  'eval_test_index': [eval_test_index]})
        results_df.append(result_df)
        
        if epoch == 150:
            results_df_tmp = pd.concat(results_df, axis=0)
            results_df_tmp.to_csv(f'result_{get_dataset_name[dataset]}_{question_type}_{question_class_size}_acc.csv', index=None)
    
    results_df = pd.concat(results_df, axis=0)
    
    if question_type == QuestionType.WHICH_ONE:
        if question_class_size != 9: 
            results_df['label_size_cand'] = counter[1]
            results_df['label_size_comp'] = counter[all_class_size - question_class_size]
        else:
            results_df['label_size_cand'] = counter[1]
            results_df['label_size_comp'] = np.nan
    elif question_type == QuestionType.IS_IN:
        if question_class_size != 5: 
            results_df['label_size_cand'] = counter[question_class_size]
            results_df['label_size_comp'] = counter[all_class_size - question_class_size]
        else:
            results_df['label_size_cand'] = counter[question_class_size]
            results_df['label_size_comp'] = np.nan
    return results_df

In [58]:
index = 'loss' #'acc' or 'loss'
for dataset_name in tqdm([DataSet.MNIST, DataSet.KMNIST, DataSet.FASHION, DataSet.CIFAR10]):#DataSet.MNIST or DataSet.KMNIST or DataSet.FASHION or Dataset.CIFAR10
    results = []
    full_random_train_loader, random_train_loader, test_loader = preparence(dataset_name, 512)
    if (dataset_name != DataSet.CIFAR10):
        model_name = 'MLP'
    else:
        model_name = 'ResNet' #'MLP' or 'ResNet'
    for itr in tqdm(range(1,6)):
        for question_type in tqdm([QuestionType.COMP]):
            if question_type == QuestionType.COMP:
                result_df = Train_Eval(index=index,
                                         dataset=dataset_name, 
                                         question_type=question_type, 
                                         question_class_size='comp', 
                                         model_name=model_name, 
                                         batch_size=800, 
                                         loss_fn=mae_loss, 
                                         EPOCHS=800)
                results.append(result_df)
            else:
                for question_size in tqdm(range(1,6)):
                        result_df = Train_Eval(index=index,
                                                 dataset=dataset_name, 
                                                 question_type=question_type, 
                                                 question_class_size=question_size, 
                                                 model_name=model_name, 
                                                 batch_size=800, 
                                                 loss_fn=mae_loss, 
                                                 EPOCHS=800)
                        results.append(result_df)
    output = pd.concat(results, axis=0)
    output.to_csv(f'all_result_{get_dataset_name[dataset_name]}_{question_type}_acc.csv', index=None)

START: QuestionType.COMP, comp
Counter({9: 10000})


TRAIN EPOCH[001/800] LOSS:1.718330%

EVAL TRAIN EPOCH[001/800] LOSS:1.521196%

EVAL TEST EPOCH[001/800] LOSS:1.522517%

TRAIN EPOCH[002/800] LOSS:1.313439%

EVAL TRAIN EPOCH[002/800] LOSS:1.095288%

EVAL TEST EPOCH[002/800] LOSS:1.092524%

TRAIN EPOCH[003/800] LOSS:0.895286%

EVAL TRAIN EPOCH[003/800] LOSS:0.792151%

EVAL TEST EPOCH[003/800] LOSS:0.782812%

TRAIN EPOCH[004/800] LOSS:0.663939%

EVAL TRAIN EPOCH[004/800] LOSS:0.666244%

EVAL TEST EPOCH[004/800] LOSS:0.655094%

TRAIN EPOCH[005/800] LOSS:0.536527%

EVAL TRAIN EPOCH[005/800] LOSS:0.588011%

EVAL TEST EPOCH[005/800] LOSS:0.585581%

TRAIN EPOCH[006/800] LOSS:0.435834%

EVAL TRAIN EPOCH[006/800] LOSS:0.531868%

EVAL TEST EPOCH[006/800] LOSS:0.533001%

TRAIN EPOCH[007/800] LOSS:0.369253%

EVAL TRAIN EPOCH[007/800] LOSS:0.498666%

EVAL TEST EPOCH[007/800] LOSS:0.503540%

TRAIN EPOCH[008/800] LOSS:0.318302%

EVAL TRAIN EPOCH[008/800] LOSS:0.477357%

EVAL TEST EPOCH[008/800] LOSS:0.485561%

TRAIN EPOCH[009/800] LOSS:0.280440%

EVA

EVAL TRAIN EPOCH[069/800] LOSS:0.426610%

EVAL TEST EPOCH[069/800] LOSS:0.449229%

TRAIN EPOCH[070/800] LOSS:0.025539%

EVAL TRAIN EPOCH[070/800] LOSS:0.426464%

EVAL TEST EPOCH[070/800] LOSS:0.449069%

TRAIN EPOCH[071/800] LOSS:0.025442%

EVAL TRAIN EPOCH[071/800] LOSS:0.426396%

EVAL TEST EPOCH[071/800] LOSS:0.448922%

TRAIN EPOCH[072/800] LOSS:0.025348%

EVAL TRAIN EPOCH[072/800] LOSS:0.426352%

EVAL TEST EPOCH[072/800] LOSS:0.448900%

TRAIN EPOCH[073/800] LOSS:0.025258%

EVAL TRAIN EPOCH[073/800] LOSS:0.426227%

EVAL TEST EPOCH[073/800] LOSS:0.448803%

TRAIN EPOCH[074/800] LOSS:0.025168%

EVAL TRAIN EPOCH[074/800] LOSS:0.426150%

EVAL TEST EPOCH[074/800] LOSS:0.448754%

TRAIN EPOCH[075/800] LOSS:0.025086%

EVAL TRAIN EPOCH[075/800] LOSS:0.426042%

EVAL TEST EPOCH[075/800] LOSS:0.448507%

TRAIN EPOCH[076/800] LOSS:0.025013%

EVAL TRAIN EPOCH[076/800] LOSS:0.425982%

EVAL TEST EPOCH[076/800] LOSS:0.448459%

TRAIN EPOCH[077/800] LOSS:0.024939%

EVAL TRAIN EPOCH[077/800] LOSS:0.425926%

TRAIN EPOCH[138/800] LOSS:0.015801%

EVAL TRAIN EPOCH[138/800] LOSS:0.420395%

EVAL TEST EPOCH[138/800] LOSS:0.445346%

TRAIN EPOCH[139/800] LOSS:0.015384%

EVAL TRAIN EPOCH[139/800] LOSS:0.417028%

EVAL TEST EPOCH[139/800] LOSS:0.441613%

TRAIN EPOCH[140/800] LOSS:0.015159%

EVAL TRAIN EPOCH[140/800] LOSS:0.416173%

EVAL TEST EPOCH[140/800] LOSS:0.440661%

TRAIN EPOCH[141/800] LOSS:0.015054%

EVAL TRAIN EPOCH[141/800] LOSS:0.415872%

EVAL TEST EPOCH[141/800] LOSS:0.440393%

TRAIN EPOCH[142/800] LOSS:0.015014%

EVAL TRAIN EPOCH[142/800] LOSS:0.415443%

EVAL TEST EPOCH[142/800] LOSS:0.440041%

TRAIN EPOCH[143/800] LOSS:0.014984%

EVAL TRAIN EPOCH[143/800] LOSS:0.415238%

EVAL TEST EPOCH[143/800] LOSS:0.439853%

TRAIN EPOCH[144/800] LOSS:0.014961%

EVAL TRAIN EPOCH[144/800] LOSS:0.415130%

EVAL TEST EPOCH[144/800] LOSS:0.439699%

TRAIN EPOCH[145/800] LOSS:0.014947%

EVAL TRAIN EPOCH[145/800] LOSS:0.415038%

EVAL TEST EPOCH[145/800] LOSS:0.439552%

TRAIN EPOCH[146/800] LOSS:0.014936%

EVA

EVAL TRAIN EPOCH[206/800] LOSS:0.416607%

EVAL TEST EPOCH[206/800] LOSS:0.438096%

TRAIN EPOCH[207/800] LOSS:0.013817%

EVAL TRAIN EPOCH[207/800] LOSS:0.416661%

EVAL TEST EPOCH[207/800] LOSS:0.438118%

TRAIN EPOCH[208/800] LOSS:0.013828%

EVAL TRAIN EPOCH[208/800] LOSS:0.416681%

EVAL TEST EPOCH[208/800] LOSS:0.438121%

TRAIN EPOCH[209/800] LOSS:0.013838%

EVAL TRAIN EPOCH[209/800] LOSS:0.416680%

EVAL TEST EPOCH[209/800] LOSS:0.438071%

TRAIN EPOCH[210/800] LOSS:0.013848%

EVAL TRAIN EPOCH[210/800] LOSS:0.416726%

EVAL TEST EPOCH[210/800] LOSS:0.438098%

TRAIN EPOCH[211/800] LOSS:0.013858%

EVAL TRAIN EPOCH[211/800] LOSS:0.416726%

EVAL TEST EPOCH[211/800] LOSS:0.438075%

TRAIN EPOCH[212/800] LOSS:0.013867%

EVAL TRAIN EPOCH[212/800] LOSS:0.416746%

EVAL TEST EPOCH[212/800] LOSS:0.438064%

TRAIN EPOCH[213/800] LOSS:0.013877%

EVAL TRAIN EPOCH[213/800] LOSS:0.416763%

EVAL TEST EPOCH[213/800] LOSS:0.438046%

TRAIN EPOCH[214/800] LOSS:0.013886%

EVAL TRAIN EPOCH[214/800] LOSS:0.416777%

...

EVAL TRAIN EPOCH[480/800] LOSS:1.416439%

EVAL TEST EPOCH[480/800] LOSS:1.431935%

TRAIN EPOCH[481/800] LOSS:0.267775%

EVAL TRAIN EPOCH[481/800] LOSS:1.427000%

EVAL TEST EPOCH[481/800] LOSS:1.441361%

TRAIN EPOCH[482/800] LOSS:0.281387%

EVAL TRAIN EPOCH[482/800] LOSS:1.421211%

EVAL TEST EPOCH[482/800] LOSS:1.432808%

TRAIN EPOCH[483/800] LOSS:0.265960%

EVAL TRAIN EPOCH[483/800] LOSS:1.417492%

EVAL TEST EPOCH[483/800] LOSS:1.429286%

TRAIN EPOCH[484/800] LOSS:0.257557%

EVAL TRAIN EPOCH[484/800] LOSS:1.418733%

EVAL TEST EPOCH[484/800] LOSS:1.430158%

TRAIN EPOCH[485/800] LOSS:0.270068%

EVAL TRAIN EPOCH[485/800] LOSS:1.441471%

EVAL TEST EPOCH[485/800] LOSS:1.446450%

TRAIN EPOCH[486/800] LOSS:0.286494%

EVAL TRAIN EPOCH[486/800] LOSS:1.431742%

EVAL TEST EPOCH[486/800] LOSS:1.430713%

TRAIN EPOCH[487/800] LOSS:0.261825%

EVAL TRAIN EPOCH[487/800] LOSS:1.409183%

EVAL TEST EPOCH[487/800] LOSS:1.423741%

TRAIN EPOCH[488/800] LOSS:0.244548%

EVAL TRAIN EPOCH[488/800] LOSS:1.417002%

TRAIN EPOCH[549/800] LOSS:0.130597%

EVAL TRAIN EPOCH[549/800] LOSS:1.440281%

EVAL TEST EPOCH[549/800] LOSS:1.453773%

TRAIN EPOCH[550/800] LOSS:0.143656%

EVAL TRAIN EPOCH[550/800] LOSS:1.441685%

EVAL TEST EPOCH[550/800] LOSS:1.457376%

TRAIN EPOCH[551/800] LOSS:0.151689%

EVAL TRAIN EPOCH[551/800] LOSS:1.434941%

EVAL TEST EPOCH[551/800] LOSS:1.457420%

TRAIN EPOCH[552/800] LOSS:0.149708%

EVAL TRAIN EPOCH[552/800] LOSS:1.430658%

EVAL TEST EPOCH[552/800] LOSS:1.448805%

TRAIN EPOCH[553/800] LOSS:0.151820%

EVAL TRAIN EPOCH[553/800] LOSS:1.419999%

EVAL TEST EPOCH[553/800] LOSS:1.432356%

TRAIN EPOCH[554/800] LOSS:0.130889%

EVAL TRAIN EPOCH[554/800] LOSS:1.430860%

EVAL TEST EPOCH[554/800] LOSS:1.444279%

TRAIN EPOCH[555/800] LOSS:0.161192%

EVAL TRAIN EPOCH[555/800] LOSS:1.434350%

EVAL TEST EPOCH[555/800] LOSS:1.448484%

TRAIN EPOCH[556/800] LOSS:0.160616%

EVAL TRAIN EPOCH[556/800] LOSS:1.435244%

EVAL TEST EPOCH[556/800] LOSS:1.457473%

TRAIN EPOCH[557/800] LOSS:0.136995%

EVA

EVAL TRAIN EPOCH[617/800] LOSS:1.409294%

EVAL TEST EPOCH[617/800] LOSS:1.430809%

TRAIN EPOCH[618/800] LOSS:0.096781%

EVAL TRAIN EPOCH[618/800] LOSS:1.425080%

EVAL TEST EPOCH[618/800] LOSS:1.452435%

TRAIN EPOCH[619/800] LOSS:0.135887%

EVAL TRAIN EPOCH[619/800] LOSS:1.469836%

EVAL TEST EPOCH[619/800] LOSS:1.498050%

TRAIN EPOCH[620/800] LOSS:0.114908%

EVAL TRAIN EPOCH[620/800] LOSS:1.421612%

EVAL TEST EPOCH[620/800] LOSS:1.442699%

TRAIN EPOCH[621/800] LOSS:0.122960%

EVAL TRAIN EPOCH[621/800] LOSS:1.425495%

EVAL TEST EPOCH[621/800] LOSS:1.430980%

TRAIN EPOCH[622/800] LOSS:0.135111%

EVAL TRAIN EPOCH[622/800] LOSS:1.421808%

EVAL TEST EPOCH[622/800] LOSS:1.420996%

TRAIN EPOCH[623/800] LOSS:0.102112%

EVAL TRAIN EPOCH[623/800] LOSS:1.420765%

EVAL TEST EPOCH[623/800] LOSS:1.438027%

TRAIN EPOCH[624/800] LOSS:0.110116%

EVAL TRAIN EPOCH[624/800] LOSS:1.428597%

EVAL TEST EPOCH[624/800] LOSS:1.439090%

TRAIN EPOCH[625/800] LOSS:0.120958%

EVAL TRAIN EPOCH[625/800] LOSS:1.425261%

TRAIN EPOCH[686/800] LOSS:0.052230%

EVAL TRAIN EPOCH[686/800] LOSS:1.415737%

EVAL TEST EPOCH[686/800] LOSS:1.440682%

TRAIN EPOCH[687/800] LOSS:0.052159%

EVAL TRAIN EPOCH[687/800] LOSS:1.416189%

EVAL TEST EPOCH[687/800] LOSS:1.441059%

TRAIN EPOCH[688/800] LOSS:0.052138%

EVAL TRAIN EPOCH[688/800] LOSS:1.416259%

EVAL TEST EPOCH[688/800] LOSS:1.441148%

TRAIN EPOCH[689/800] LOSS:0.052122%

EVAL TRAIN EPOCH[689/800] LOSS:1.416283%

EVAL TEST EPOCH[689/800] LOSS:1.441228%

TRAIN EPOCH[690/800] LOSS:0.052110%

EVAL TRAIN EPOCH[690/800] LOSS:1.416318%

EVAL TEST EPOCH[690/800] LOSS:1.441320%

TRAIN EPOCH[691/800] LOSS:0.052100%

EVAL TRAIN EPOCH[691/800] LOSS:1.416368%

EVAL TEST EPOCH[691/800] LOSS:1.441414%

TRAIN EPOCH[692/800] LOSS:0.052093%

EVAL TRAIN EPOCH[692/800] LOSS:1.416427%

EVAL TEST EPOCH[692/800] LOSS:1.441500%

TRAIN EPOCH[693/800] LOSS:0.052086%

EVAL TRAIN EPOCH[693/800] LOSS:1.416493%

EVAL TEST EPOCH[693/800] LOSS:1.441579%

TRAIN EPOCH[694/800] LOSS:0.052080%

EVA

EVAL TRAIN EPOCH[754/800] LOSS:1.415436%

EVAL TEST EPOCH[754/800] LOSS:1.439018%

TRAIN EPOCH[755/800] LOSS:0.051952%

EVAL TRAIN EPOCH[755/800] LOSS:1.415073%

EVAL TEST EPOCH[755/800] LOSS:1.441084%

TRAIN EPOCH[756/800] LOSS:0.051980%

EVAL TRAIN EPOCH[756/800] LOSS:1.421883%

EVAL TEST EPOCH[756/800] LOSS:1.448286%

TRAIN EPOCH[757/800] LOSS:0.052018%

EVAL TRAIN EPOCH[757/800] LOSS:1.415727%

EVAL TEST EPOCH[757/800] LOSS:1.442059%

TRAIN EPOCH[758/800] LOSS:0.052023%

EVAL TRAIN EPOCH[758/800] LOSS:1.416886%

EVAL TEST EPOCH[758/800] LOSS:1.438307%

TRAIN EPOCH[759/800] LOSS:0.051995%

EVAL TRAIN EPOCH[759/800] LOSS:1.414954%

EVAL TEST EPOCH[759/800] LOSS:1.438553%

TRAIN EPOCH[760/800] LOSS:0.051972%

EVAL TRAIN EPOCH[760/800] LOSS:1.414942%

EVAL TEST EPOCH[760/800] LOSS:1.439083%

TRAIN EPOCH[761/800] LOSS:0.051961%

EVAL TRAIN EPOCH[761/800] LOSS:1.414928%

EVAL TEST EPOCH[761/800] LOSS:1.440141%

TRAIN EPOCH[762/800] LOSS:0.051957%

EVAL TRAIN EPOCH[762/800] LOSS:1.415599%

In [60]:
index = 'loss' #'acc' or 'loss'
for dataset_name in tqdm([DataSet.CIFAR10]):#DataSet.MNIST or DataSet.KMNIST or DataSet.FASHION or Dataset.CIFAR10
    results = []
    full_random_train_loader, random_train_loader, test_loader = preparence(dataset_name, 512)
    if (dataset_name != DataSet.CIFAR10):
        model_name = 'MLP'
    else:
        model_name = 'ResNet' #'MLP' or 'ResNet'
    for itr in tqdm(range(1,6)):
        for question_type in tqdm([QuestionType.WHICH_ONE]):
            if question_type == QuestionType.COMP:
                result_df = Train_Eval(index=index,
                                         dataset=dataset_name, 
                                         question_type=question_type, 
                                         question_class_size='comp', 
                                         model_name=model_name, 
                                         batch_size=800, 
                                         loss_fn=mae_loss, 
                                         EPOCHS=800)
                results.append(result_df)
            else:
                for question_size in tqdm(range(6,10)):
                        result_df = Train_Eval(index=index,
                                                 dataset=dataset_name, 
                                                 question_type=question_type, 
                                                 question_class_size=question_size, 
                                                 model_name=model_name, 
                                                 batch_size=800, 
                                                 loss_fn=mae_loss, 
                                                 EPOCHS=800)
                        results.append(result_df)
    output = pd.concat(results, axis=0)
    output.to_csv(f'all_result_{get_dataset_name[dataset_name]}_{question_type}_acc.csv', index=None)

Files already downloaded and verified


START: QuestionType.WHICH_ONE, 6
Counter({1: 5996, 4: 4004})


TRAIN EPOCH[001/800] LOSS:1.113048%

EVAL TRAIN EPOCH[001/800] LOSS:1.102820%

EVAL TEST EPOCH[001/800] LOSS:1.143118%

TRAIN EPOCH[002/800] LOSS:0.675489%

EVAL TRAIN EPOCH[002/800] LOSS:0.700162%

EVAL TEST EPOCH[002/800] LOSS:0.797261%

TRAIN EPOCH[003/800] LOSS:0.579377%

EVAL TRAIN EPOCH[003/800] LOSS:0.670682%

EVAL TEST EPOCH[003/800] LOSS:0.795522%

TRAIN EPOCH[004/800] LOSS:0.522180%

EVAL TRAIN EPOCH[004/800] LOSS:0.539835%

EVAL TEST EPOCH[004/800] LOSS:0.690979%

TRAIN EPOCH[005/800] LOSS:0.481416%

EVAL TRAIN EPOCH[005/800] LOSS:0.493362%

EVAL TEST EPOCH[005/800] LOSS:0.662846%

TRAIN EPOCH[006/800] LOSS:0.436383%

EVAL TRAIN EPOCH[006/800] LOSS:0.494909%

EVAL TEST EPOCH[006/800] LOSS:0.669923%

TRAIN EPOCH[007/800] LOSS:0.415388%

EVAL TRAIN EPOCH[007/800] LOSS:0.501113%

EVAL TEST EPOCH[007/800] LOSS:0.686748%

TRAIN EPOCH[008/800] LOSS:0.408627%

EVAL TRAIN EPOCH[008/800] LOSS:0.448822%

EVAL TEST EPOCH[008/800] LOSS:0.648708%

TRAIN EPOCH[009/800] LOSS:0.386108%

EVA

EVAL TRAIN EPOCH[069/800] LOSS:0.183908%

EVAL TEST EPOCH[069/800] LOSS:0.549592%

TRAIN EPOCH[070/800] LOSS:0.088444%

EVAL TRAIN EPOCH[070/800] LOSS:0.177392%

EVAL TEST EPOCH[070/800] LOSS:0.543941%

TRAIN EPOCH[071/800] LOSS:0.099578%

EVAL TRAIN EPOCH[071/800] LOSS:0.192074%

EVAL TEST EPOCH[071/800] LOSS:0.568319%

TRAIN EPOCH[072/800] LOSS:0.088008%

EVAL TRAIN EPOCH[072/800] LOSS:0.184647%

EVAL TEST EPOCH[072/800] LOSS:0.545829%

TRAIN EPOCH[073/800] LOSS:0.105951%

EVAL TRAIN EPOCH[073/800] LOSS:0.202489%

EVAL TEST EPOCH[073/800] LOSS:0.567185%

TRAIN EPOCH[074/800] LOSS:0.110816%

EVAL TRAIN EPOCH[074/800] LOSS:0.206337%

EVAL TEST EPOCH[074/800] LOSS:0.573300%

TRAIN EPOCH[075/800] LOSS:0.104451%

EVAL TRAIN EPOCH[075/800] LOSS:0.189855%

EVAL TEST EPOCH[075/800] LOSS:0.562600%

TRAIN EPOCH[076/800] LOSS:0.105291%

EVAL TRAIN EPOCH[076/800] LOSS:0.200076%

EVAL TEST EPOCH[076/800] LOSS:0.573233%

TRAIN EPOCH[077/800] LOSS:0.100752%

EVAL TRAIN EPOCH[077/800] LOSS:0.204265%

TRAIN EPOCH[138/800] LOSS:0.065390%

EVAL TRAIN EPOCH[138/800] LOSS:0.162403%

EVAL TEST EPOCH[138/800] LOSS:0.552839%

TRAIN EPOCH[139/800] LOSS:0.063705%

EVAL TRAIN EPOCH[139/800] LOSS:0.156467%

EVAL TEST EPOCH[139/800] LOSS:0.545175%

TRAIN EPOCH[140/800] LOSS:0.061460%

EVAL TRAIN EPOCH[140/800] LOSS:0.183304%

EVAL TEST EPOCH[140/800] LOSS:0.583976%

TRAIN EPOCH[141/800] LOSS:0.061666%

EVAL TRAIN EPOCH[141/800] LOSS:0.163078%

EVAL TEST EPOCH[141/800] LOSS:0.557133%

TRAIN EPOCH[142/800] LOSS:0.063571%

EVAL TRAIN EPOCH[142/800] LOSS:0.161214%

EVAL TEST EPOCH[142/800] LOSS:0.566854%

TRAIN EPOCH[143/800] LOSS:0.067023%

EVAL TRAIN EPOCH[143/800] LOSS:0.167367%

EVAL TEST EPOCH[143/800] LOSS:0.564096%

TRAIN EPOCH[144/800] LOSS:0.073451%

EVAL TRAIN EPOCH[144/800] LOSS:0.170744%

EVAL TEST EPOCH[144/800] LOSS:0.559286%

TRAIN EPOCH[145/800] LOSS:0.073217%

EVAL TRAIN EPOCH[145/800] LOSS:0.180289%

EVAL TEST EPOCH[145/800] LOSS:0.584289%

TRAIN EPOCH[146/800] LOSS:0.069975%

EVA

...

EVAL TRAIN EPOCH[480/800] LOSS:0.044255%

EVAL TEST EPOCH[480/800] LOSS:0.575354%

TRAIN EPOCH[481/800] LOSS:0.033569%

EVAL TRAIN EPOCH[481/800] LOSS:0.059924%

EVAL TEST EPOCH[481/800] LOSS:0.594185%

TRAIN EPOCH[482/800] LOSS:0.035204%

EVAL TRAIN EPOCH[482/800] LOSS:0.037800%

EVAL TEST EPOCH[482/800] LOSS:0.581427%

TRAIN EPOCH[483/800] LOSS:0.035405%

EVAL TRAIN EPOCH[483/800] LOSS:0.061810%

EVAL TEST EPOCH[483/800] LOSS:0.619741%

TRAIN EPOCH[484/800] LOSS:0.034938%

EVAL TRAIN EPOCH[484/800] LOSS:0.041030%

EVAL TEST EPOCH[484/800] LOSS:0.588346%

TRAIN EPOCH[485/800] LOSS:0.030834%

EVAL TRAIN EPOCH[485/800] LOSS:0.036728%

EVAL TEST EPOCH[485/800] LOSS:0.571048%

TRAIN EPOCH[486/800] LOSS:0.026798%

EVAL TRAIN EPOCH[486/800] LOSS:0.030421%

EVAL TEST EPOCH[486/800] LOSS:0.574726%

TRAIN EPOCH[487/800] LOSS:0.032927%

EVAL TRAIN EPOCH[487/800] LOSS:0.035090%

EVAL TEST EPOCH[487/800] LOSS:0.563122%

TRAIN EPOCH[488/800] LOSS:0.035616%

EVAL TRAIN EPOCH[488/800] LOSS:0.040832%

TRAIN EPOCH[549/800] LOSS:0.014213%

EVAL TRAIN EPOCH[549/800] LOSS:0.016012%

EVAL TEST EPOCH[549/800] LOSS:0.547742%

TRAIN EPOCH[550/800] LOSS:0.014634%

EVAL TRAIN EPOCH[550/800] LOSS:0.016262%

EVAL TEST EPOCH[550/800] LOSS:0.547280%

TRAIN EPOCH[551/800] LOSS:0.014708%

EVAL TRAIN EPOCH[551/800] LOSS:0.016795%

EVAL TEST EPOCH[551/800] LOSS:0.541463%

TRAIN EPOCH[552/800] LOSS:0.014414%

EVAL TRAIN EPOCH[552/800] LOSS:0.014912%

EVAL TEST EPOCH[552/800] LOSS:0.537908%

TRAIN EPOCH[553/800] LOSS:0.014200%

EVAL TRAIN EPOCH[553/800] LOSS:0.016259%

EVAL TEST EPOCH[553/800] LOSS:0.546199%

TRAIN EPOCH[554/800] LOSS:0.014628%

EVAL TRAIN EPOCH[554/800] LOSS:0.016550%

EVAL TEST EPOCH[554/800] LOSS:0.547346%

TRAIN EPOCH[555/800] LOSS:0.015473%

EVAL TRAIN EPOCH[555/800] LOSS:0.016465%

EVAL TEST EPOCH[555/800] LOSS:0.549181%

TRAIN EPOCH[556/800] LOSS:0.015615%

EVAL TRAIN EPOCH[556/800] LOSS:0.016804%

EVAL TEST EPOCH[556/800] LOSS:0.549826%

TRAIN EPOCH[557/800] LOSS:0.014897%

EVA

EVAL TRAIN EPOCH[617/800] LOSS:0.026025%

EVAL TEST EPOCH[617/800] LOSS:0.575094%

TRAIN EPOCH[618/800] LOSS:0.020878%

EVAL TRAIN EPOCH[618/800] LOSS:0.025154%

EVAL TEST EPOCH[618/800] LOSS:0.571656%

TRAIN EPOCH[619/800] LOSS:0.025319%

EVAL TRAIN EPOCH[619/800] LOSS:0.053889%

EVAL TEST EPOCH[619/800] LOSS:0.603623%

TRAIN EPOCH[620/800] LOSS:0.028673%

EVAL TRAIN EPOCH[620/800] LOSS:0.042437%

EVAL TEST EPOCH[620/800] LOSS:0.595300%

TRAIN EPOCH[621/800] LOSS:0.033999%

EVAL TRAIN EPOCH[621/800] LOSS:0.031475%

EVAL TEST EPOCH[621/800] LOSS:0.578537%

TRAIN EPOCH[622/800] LOSS:0.030577%

EVAL TRAIN EPOCH[622/800] LOSS:0.039329%

EVAL TEST EPOCH[622/800] LOSS:0.584131%

TRAIN EPOCH[623/800] LOSS:0.025113%

EVAL TRAIN EPOCH[623/800] LOSS:0.044268%

EVAL TEST EPOCH[623/800] LOSS:0.586726%

TRAIN EPOCH[624/800] LOSS:0.027226%

EVAL TRAIN EPOCH[624/800] LOSS:0.039079%

EVAL TEST EPOCH[624/800] LOSS:0.587405%

TRAIN EPOCH[625/800] LOSS:0.035972%

EVAL TRAIN EPOCH[625/800] LOSS:0.035704%

TRAIN EPOCH[686/800] LOSS:0.015180%

EVAL TRAIN EPOCH[686/800] LOSS:0.018358%

EVAL TEST EPOCH[686/800] LOSS:0.563381%

TRAIN EPOCH[687/800] LOSS:0.018239%

EVAL TRAIN EPOCH[687/800] LOSS:0.023145%

EVAL TEST EPOCH[687/800] LOSS:0.573563%

TRAIN EPOCH[688/800] LOSS:0.017904%

EVAL TRAIN EPOCH[688/800] LOSS:0.019027%

EVAL TEST EPOCH[688/800] LOSS:0.566584%

TRAIN EPOCH[689/800] LOSS:0.015292%

EVAL TRAIN EPOCH[689/800] LOSS:0.017848%

EVAL TEST EPOCH[689/800] LOSS:0.567056%

TRAIN EPOCH[690/800] LOSS:0.016805%

EVAL TRAIN EPOCH[690/800] LOSS:0.024566%

EVAL TEST EPOCH[690/800] LOSS:0.575642%

TRAIN EPOCH[691/800] LOSS:0.021028%

EVAL TRAIN EPOCH[691/800] LOSS:0.028352%

EVAL TEST EPOCH[691/800] LOSS:0.581737%

TRAIN EPOCH[692/800] LOSS:0.022648%

EVAL TRAIN EPOCH[692/800] LOSS:0.027401%

EVAL TEST EPOCH[692/800] LOSS:0.599648%

TRAIN EPOCH[693/800] LOSS:0.023970%

EVAL TRAIN EPOCH[693/800] LOSS:0.025783%

EVAL TEST EPOCH[693/800] LOSS:0.579130%

TRAIN EPOCH[694/800] LOSS:0.021522%

EVA

EVAL TRAIN EPOCH[754/800] LOSS:0.047030%

EVAL TEST EPOCH[754/800] LOSS:0.603101%

TRAIN EPOCH[755/800] LOSS:0.034989%

EVAL TRAIN EPOCH[755/800] LOSS:0.029987%

EVAL TEST EPOCH[755/800] LOSS:0.585456%

TRAIN EPOCH[756/800] LOSS:0.024210%

EVAL TRAIN EPOCH[756/800] LOSS:0.026854%

EVAL TEST EPOCH[756/800] LOSS:0.571835%

TRAIN EPOCH[757/800] LOSS:0.023405%

EVAL TRAIN EPOCH[757/800] LOSS:0.023226%

EVAL TEST EPOCH[757/800] LOSS:0.554564%

TRAIN EPOCH[758/800] LOSS:0.020765%

EVAL TRAIN EPOCH[758/800] LOSS:0.026654%

EVAL TEST EPOCH[758/800] LOSS:0.559821%

TRAIN EPOCH[759/800] LOSS:0.021745%

EVAL TRAIN EPOCH[759/800] LOSS:0.020732%

EVAL TEST EPOCH[759/800] LOSS:0.559446%

TRAIN EPOCH[760/800] LOSS:0.018260%

EVAL TRAIN EPOCH[760/800] LOSS:0.025601%

EVAL TEST EPOCH[760/800] LOSS:0.570982%

TRAIN EPOCH[761/800] LOSS:0.019604%

EVAL TRAIN EPOCH[761/800] LOSS:0.021417%

EVAL TEST EPOCH[761/800] LOSS:0.575062%

TRAIN EPOCH[762/800] LOSS:0.023821%

EVAL TRAIN EPOCH[762/800] LOSS:0.030763%